In [21]:
import os
import sys
import pywFM
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

NumberOfRows = 10000

os.environ['LIBFM_PATH'] = os.path.expanduser('/home/jovyan/work/libfm/bin/')
filePath = os.getcwd() + '/yelp_dataset/'
print(filePath)
pd.set_option('display.max_columns', None)
%matplotlib inline

/home/jovyan/work/Personalization/yelp_dataset/


https://github.com/jfloff/pywFM

In [2]:
businuessColumns = ['state', 'business_id'] #'review_count', 'stars', 
userColumns = ["user_id", "average_stars", "review_count"] #, "elite", "compliment_photos", "compliment_list", "compliment_funny", "compliment_plain", "compliment_note", "compliment_writer", "compliment_cute", "compliment_more", "compliment_hot", "compliment_profile", "compliment_cool", "useful", "fans", "funny", "cool", 
ratingsColumns = ["business_id", "stars", "user_id"] #"cool", "funny", "useful", 
targetColumn = "stars"

In [3]:
os.listdir(filePath)

['.DS_Store',
 'yelp_ratings.csv',
 'textTransform.npz',
 'business_cleaned.csv',
 'review_cleaned_withTrainTest.csv',
 'user_cleaned.csv',
 'tfidfTransformer.pkl',
 '.ipynb_checkpoints',
 'countVectorizer.pkl']

In [4]:
business = pd.read_csv(filePath + "business_cleaned.csv", usecols=businuessColumns)
user = pd.read_csv(filePath + 'user_cleaned.csv', usecols=userColumns)
ratings = pd.read_csv(filePath + 'review_cleaned_withTrainTest.csv', nrows=NumberOfRows)

### Check duplicates and NaNs

In [5]:
ratings.drop_duplicates().shape, ratings.shape

((10000, 10), (10000, 10))

In [6]:
duplicateDF = ratings.loc[ratings[['user_id', 'business_id']].duplicated()]
x = ratings.loc[
    ratings["business_id"].isin(duplicateDF["business_id"]) & ratings["user_id"].isin(duplicateDF['user_id'])
].sort_values(["user_id", "business_id", "stars"])[["user_id", "business_id", "review_id", "date", "stars", "text"]]
print(x.shape)
x

(0, 6)


Empty DataFrame
Columns: [user_id, business_id, review_id, date, stars, text]
Index: []

In [7]:
ratings.isnull().values.sum()

0

### Concatenate DataFrames

In [8]:
ratings = pd.merge(ratings, business, how='left', left_on='business_id', right_on='business_id')
ratings = pd.merge(ratings, user, how='left', left_on='user_id', right_on='user_id')

In [9]:
ratings['business_id'] = ratings['business_id'].astype('category')
ratings['business_id'] = ratings['business_id'].cat.codes

ratings['user_id'] = ratings['user_id'].astype('category')
ratings['user_id'] = ratings['user_id'].cat.codes

In [10]:
ratings.head()

user_id                 date  business_id  cool  funny  \
0     1109  2015-01-01 00:00:30         5849   0.0    0.0   
1     3246  2015-01-01 00:02:20         3694   0.0    0.0   
2     5243  2015-01-01 00:02:35         2664   0.0    1.0   
3       29  2015-01-01 00:02:42         5565   0.0    0.0   
4     5941  2015-01-01 00:04:13         5235   1.0    0.0   

                review_id  stars  \
0  hNwleSHcvNksIQT31569Yg    5.0   
1  DfZGAhAkPMJYDdXGRjhw8A    2.0   
2  65viXwIysYSxEyPZgRSVbQ    1.0   
3  hS3phsfoP-fAZVlMomx4Kg    5.0   
4  eaDgBBrOtvFUto5pADZwQA    5.0   

                                                text  useful  TrainTest state  \
0  Window washing inside and out done after many ...     5.0          1    NV   
1  I will admit, I do not have high expectations ...     0.0          0    AZ   
2  The chicken curry I got was extremely dry. Des...     0.0          1    ON   
3  Really took care of me on my trip out of state...     0.0          0    AZ   
4  Gary and Chester run this 2 year old Church St...     1.0          0    ON   

   review_count  average_stars  
0            21           4.79  
1            30           3.80  
2            19           2.68  
3             9           3.33  
4             6           4.00

In [12]:
def convertDummies(df, column_name):
    df = pd.concat([
        df.drop(column_name, axis=1),
        pd.get_dummies(df[column_name], prefix=column_name+'_')
    ], axis=1)
    print(column_name, ' is ready.')
    return df

In [13]:
ratings = convertDummies(ratings, 'business_id')
ratings = convertDummies(ratings, 'user_id')
ratings = convertDummies(ratings, 'state')

business_id  is ready.
user_id  is ready.
state  is ready.


In [11]:
ratings.drop(['text', 'review_id', 'date'], axis=1, inplace=True)

In [14]:
ratings.head()

cool  funny  stars  useful  TrainTest  review_count  average_stars  \
0   0.0    0.0    5.0     5.0          1            21           4.79   
1   0.0    0.0    2.0     0.0          0            30           3.80   
2   0.0    1.0    1.0     0.0          1            19           2.68   
3   0.0    0.0    5.0     0.0          0             9           3.33   
4   1.0    0.0    5.0     1.0          0             6           4.00   

   business_id__0  business_id__1  business_id__2  business_id__3  \
0               0               0               0               0   
1               0               0               0               0   
2               0               0               0               0   
3               0               0               0               0   
4               0               0               0               0   

   business_id__4  business_id__5  business_id__6  business_id__7  \
0               0               0               0               0   
1               0               0               0               0   
2               0               0               0               0   
3               0               0               0               0   
4               0               0               0               0   

   business_id__8  business_id__9  business_id__10  business_id__11  \
0               0               0                0                0   
1               0               0                0                0   
2               0               0                0                0   
3               0               0                0                0   
4               0               0                0                0   

   business_id__12  business_id__13  business_id__14  business_id__15  \
0                0                0                0                0   
1                0                0                0                0   
2                0                0                0                0   
3                0                0                0                0   
4                0                0                0                0   

   business_id__16  business_id__17  business_id__18  business_id__19  \
0                0                0                0                0   
1                0                0                0                0   
2                0                0                0                0   
3                0                0                0                0   
4                0                0                0                0   

   business_id__20  business_id__21  business_id__22  business_id__23  \
0                0                0                0                0   
1                0                0                0                0   
2                0                0                0                0   
3                0                0                0                0   
4                0                0                0                0   

   business_id__24  business_id__25  business_id__26  business_id__27  \
0                0                0                0                0   
1                0                0                0                0   
2                0                0                0                0   
3                0                0                0                0   
4                0                0                0                0   

   business_id__28  business_id__29  business_id__30  business_id__31  \
0                0                0                0                0   
1                0                0                0                0   
2                0                0                0                0   
3                0                0                0                0   
4                0                0                0                0   

   business_id__32  business_id__33  business_id__34  business_id__35  \
0                0                0    

In [16]:
train_X = ratings.loc[ratings['TrainTest'] == 1].drop(targetColumn, axis=1).drop('TrainTest', axis=1)
train_y = ratings.loc[ratings['TrainTest'] == 1][targetColumn]

test_X = ratings.loc[ratings['TrainTest'] == 0].drop(targetColumn, axis=1).drop('TrainTest', axis=1)
test_y = ratings.loc[ratings['TrainTest'] == 0][targetColumn]

In [17]:
train_X.shape, train_y.shape

((8554, 13570), (8554,))

In [18]:
test_X.shape, test_y.shape

((1446, 13570), (1446,))

In [22]:
fm = pywFM.FM(task='regression')
model = fm.run(train_X.values, train_y.values, test_X.values, test_y.values)

In [23]:
pd.concat([test_y.reset_index(drop=True), pd.Series(model.predictions, name='predicted')], axis=1).head()

stars  predicted
0    2.0    3.77633
1    5.0    3.55053
2    5.0    3.76915
3    3.0    3.69605
4    2.0    3.34754

In [24]:
from sklearn.metrics import mean_squared_error
np.sqrt(mean_squared_error(test_y.values, model.predictions))

1.4930535556340547

In [25]:
np.sqrt(mean_squared_error(test_y.values, np.tile(ratings['stars'].mean(), test_y.shape[0])))

1.5164853250228574